In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "5"
os.environ['PYOPENGL_PLATFORM'] = 'egl'

import mesh_to_sdf
from os import path
import h5py
import numpy as np
import trimesh
import multiprocessing as mp
import time

In [2]:
mesh_dir = '../dataGeneration_vF/data/meshes_coll'
save_dir = 'evals/shape/gt'

dx = np.linspace(-.2, .2, 100)
X, Y, Z = np.meshgrid(dx, dx, dx, indexing='ij')
grid = np.stack([X.flatten(), Y.flatten(), Z.flatten()]).transpose()

def start_process():
    print('Starting', mp.current_process().name)

def saveEvalData(filename):
    print(filename)
    
    
    obj_trimesh = trimesh.load(path.join(mesh_dir, filename))
    point_cloud = mesh_to_sdf.get_surface_point_cloud(obj_trimesh,
                                                      bounding_radius=0.2)
    surface_points = point_cloud.get_random_surface_points(10000)
    sdf = point_cloud.get_sdf_in_batches(grid, 
                                         use_depth_buffer=True, 
                                         sample_count=10000000)
    
    data = h5py.File(path.join(save_dir, path.splitext(filename)[0]+'.hdf5'), mode='w')
    data.create_dataset("surface_points", data=surface_points)
    data.create_dataset("sdf", data=sdf)
    data.close()
filename_list = [fn for fn in os.listdir(mesh_dir) if fn.endswith('.obj')]

t = time.time()
pool = mp.Pool(processes=66,
               initializer=start_process)
outputs = pool.map(saveEvalData, filename_list)

pool.close() # no more tasks
pool.join()  # wrap up current tasks
print(time.time() - t)

Starting ForkPoolWorker-1
Starting ForkPoolWorker-2
Starting ForkPoolWorker-4
Starting ForkPoolWorker-5Starting 
ForkPoolWorker-6
StartingStarting  ForkPoolWorker-7ForkPoolWorker-3
Starting
 ForkPoolWorker-8
Starting ForkPoolWorker-9Starting
 ForkPoolWorker-10
Starting ForkPoolWorker-11
Starting StartingForkPoolWorker-12
 ForkPoolWorker-13Starting
 ForkPoolWorker-14Starting
 ForkPoolWorker-15
Starting ForkPoolWorker-16Starting
 ForkPoolWorker-17
Starting Starting ForkPoolWorker-18ForkPoolWorker-19

Starting ForkPoolWorker-20Starting
 ForkPoolWorker-21
Starting ForkPoolWorker-22
 StartingForkPoolWorker-23
Starting ForkPoolWorker-24
Starting ForkPoolWorker-25Starting 
ForkPoolWorker-26
Starting ForkPoolWorker-27
Starting ForkPoolWorker-28Starting
 ForkPoolWorker-29
Starting ForkPoolWorker-30 ForkPoolWorker-31Starting

Starting ForkPoolWorker-32
Starting ForkPoolWorker-33
Starting ForkPoolWorker-34
Starting ForkPoolWorker-36
StartingStarting  ForkPoolWorker-37
ForkPoolWorker-35
Starting F

In [1]:
# %matplotlib widget
import os
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "4"
os.environ['PYOPENGL_PLATFORM']= 'egl'

from src.vector_object import *

from src.frame import Frame

from src.feature import SDF_Feature
from src.dataset import *
from src.utils import *
from src.data_gen_utils import *

from os import path
from tqdm.notebook import tqdm
import matplotlib.pyplot as plt

import trimesh

In [2]:
device = "cuda" if torch.cuda.is_available() else "cpu"
exp_name = 'PIFO_best'
state = torch.load('network/'+exp_name+'.pth.tar')
C = state['config']

trainset = PIFODataset(C['DATA_FILENAME'],
                       num_views=C['NUM_VIEWS'],
                       num_points=C['NUM_POINTS'],
                       num_grasps=C['NUM_GRASPS'],
                       num_hangs=C['NUM_HANGS'],
                       grasp_draw_points=C['GRASP_DRAW_POINTS'],
                       hang_draw_points=C['HANG_DRAW_POINTS'],
                       random_erase=False,
                       on_gpu_memory=True)

testset = PIFODataset('data/test_batch.hdf5',
                      num_views=C['NUM_VIEWS'],
                      num_points=C['NUM_POINTS'],
                      num_grasps=C['NUM_GRASPS'],
                      num_hangs=C['NUM_HANGS'],
                      grasp_draw_points=C['GRASP_DRAW_POINTS'],
                      hang_draw_points=C['HANG_DRAW_POINTS'],
                      random_erase=False,
                      on_gpu_memory=True)


warper = RandomImageWarper(img_res=C['IMG_RES'], 
                           sig_center=0, 
                           return_cam_params=True)

# PIFO
obj1 = Frame()
obj1.build_backbone(pretrained=True, **C)
obj1.build_sdf_head(C['SDF_HEAD_HIDDEN'])
obj1.build_keypoint_head('grasp', C['GRASP_HEAD_HIDDEN'], C['GRIPPER_POINTS'])
obj1.build_keypoint_head('hang', C['HANG_HEAD_HIDDEN'], C['HOOK_POINTS'])
obj1.load_state_dict(state['network'])
obj1.to(device).eval()
F_sdf1 = SDF_Feature(obj1)


# noPixel
exp_name = 'noPixelAligned_best'
state = torch.load('network/'+exp_name+'.pth.tar')
C = state['config']
obj2 = Frame()
obj2.build_backbone(pretrained=True, **C)
obj2.build_sdf_head(C['SDF_HEAD_HIDDEN'])
obj2.build_keypoint_head('grasp', C['GRASP_HEAD_HIDDEN'], C['GRIPPER_POINTS'])
obj2.build_keypoint_head('hang', C['HANG_HEAD_HIDDEN'], C['HOOK_POINTS'])
obj2.load_state_dict(state['network'])
obj2.to(device).eval()
F_sdf2 = SDF_Feature(obj2)


# vecObj
exp_name = 'vectorObject_best'
state = torch.load('network/'+exp_name+'.pth.tar')
C = state['config']
obj3 = Frame_vec()
obj3.build_backbone(pretrained=True, **C)
obj3.build_sdf_head(C['SDF_HEAD_HIDDEN'])
obj3.build_pose_head('grasp', C['GRASP_HEAD_HIDDEN'])
obj3.build_pose_head('hang', C['HANG_HEAD_HIDDEN'])
obj3.load_state_dict(state['network'])
obj3.to(device).eval()
F_sdf3 = SDF_Feature_vec(obj3)

In [4]:
with torch.no_grad():
    for num_views in [2,8]:
        for dataset in [trainset, testset]:
            dataset.num_views = num_views
            for i, data in enumerate(dataset):
                data = to_device(data, device)
                rgb, projections, cam_pos, new_origin, cam_roll = warper(data['rgb'].unsqueeze(0), 
                                      data['cam_extrinsic'].unsqueeze(0), 
                                      data['cam_intrinsic'].unsqueeze(0))

                vertices, faces, normals, sdf = obj1.extract_mesh(rgb,
                                                            projections, 
                                                            scale=.2, 
                                                            delta=0.00,
                                                            num_grid=100,
                                                            sdf_scale=C['SDF_SCALE'],
                                                            draw=False,
                                                            return_sdf=True)

                save_dir = 'evals/shape/PIFO_'+str(num_views)
                os.makedirs(save_dir, exist_ok=True)
                os.makedirs(save_dir+'_recon', exist_ok=True)
                trimesh.Trimesh(vertices=vertices, faces=faces).export(path.join(save_dir+'_recon', data['filenames']))

                f = h5py.File(path.join(save_dir, path.splitext(data['filenames'])[0]+'.hdf5'), mode='w')
                f.create_dataset("sdf", data=sdf)
                f.close()

                vertices, faces, normals, sdf = obj2.extract_mesh(rgb,
                                                            projections, 
                                                            scale=.2, 
                                                            delta=0.00,
                                                            num_grid=100,
                                                            sdf_scale=C['SDF_SCALE'],
                                                            draw=False,
                                                            return_sdf=True)
                save_dir = 'evals/shape/noPixel_'+str(num_views)
                os.makedirs(save_dir, exist_ok=True)
                os.makedirs(save_dir+'_recon', exist_ok=True)
                trimesh.Trimesh(vertices=vertices, faces=faces).export(path.join(save_dir+'_recon', data['filenames']))

                f = h5py.File(path.join(save_dir, path.splitext(data['filenames'])[0]+'.hdf5'), mode='w')
                f.create_dataset("sdf", data=sdf)
                f.close()

                vertices, faces, normals, sdf = obj3.extract_mesh(rgb,
                                                            torch.cat([cam_pos, cam_roll], dim=2),
                                                            scale=.2, 
                                                            delta=0.001,
                                                            num_grid=100,
                                                            sdf_scale=C['SDF_SCALE'],
                                                            draw=False,
                                                            return_sdf=True)
                save_dir = 'evals/shape/vecObj_'+str(num_views)
                os.makedirs(save_dir, exist_ok=True)
                os.makedirs(save_dir+'_recon', exist_ok=True)

                trimesh.Trimesh(vertices=vertices, faces=faces).export(path.join(save_dir+'_recon', data['filenames']))
                f = h5py.File(path.join(save_dir, path.splitext(data['filenames'])[0]+'.hdf5'), mode='w')
                f.create_dataset("sdf", data=sdf)
                f.close()

In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "5"
os.environ['PYOPENGL_PLATFORM'] = 'egl'

import mesh_to_sdf
from os import path
import h5py
import numpy as np
import trimesh
import multiprocessing as mp
import time

In [10]:
with h5py.File('data/split.hdf5', 'r') as f:
    train_list = f['train'][:]
    test_list = f['test'][:]
    
filename_list = train_list.tolist()+test_list.tolist()

for num_views in [2,8]:
    for exp_name in ['PIFO', 'noPixel', 'vecObj']:

        save_dir = 'evals/shape/'+exp_name+'_'+str(num_views)
        mesh_dir = save_dir+'_recon'

        def start_process():
            print('Starting', mp.current_process().name)

        def saveEvalData(filename):
            print(filename)


            obj_trimesh = trimesh.load(path.join(mesh_dir, filename))
            point_cloud = mesh_to_sdf.get_surface_point_cloud(obj_trimesh,
                                                              bounding_radius=0.2)
            surface_points = point_cloud.get_random_surface_points(10000)

            data = h5py.File(path.join(save_dir, path.splitext(filename)[0]+'.hdf5'), mode='r+')
            data.create_dataset("surface_points", data=surface_points)
            data.close()

        t = time.time()
        pool = mp.Pool(processes=32,
                       initializer=start_process)
        outputs = pool.map(saveEvalData, filename_list)

        pool.close() # no more tasks
        pool.join()  # wrap up current tasks
        print(time.time() - t)

Starting ForkPoolWorker-1
Starting ForkPoolWorker-2
Starting ForkPoolWorker-5
Starting StartingForkPoolWorker-6 
ForkPoolWorker-7
Starting ForkPoolWorker-8StartingStartingStarting
   ForkPoolWorker-9ForkPoolWorker-3

ForkPoolWorker-4Starting
 ForkPoolWorker-10
Starting ForkPoolWorker-11
Starting ForkPoolWorker-12
Starting ForkPoolWorker-13
Starting ForkPoolWorker-14
Starting ForkPoolWorker-15Starting 
ForkPoolWorker-16
Starting ForkPoolWorker-17
Starting ForkPoolWorker-18
Starting ForkPoolWorker-19
Starting ForkPoolWorker-20
Starting ForkPoolWorker-21Starting
 ForkPoolWorker-22Starting
 ForkPoolWorker-23Starting 
ForkPoolWorker-24
Starting ForkPoolWorker-25
Starting ForkPoolWorker-26
Starting ForkPoolWorker-27
Starting ForkPoolWorker-28
Starting ForkPoolWorker-29Starting
 ForkPoolWorker-30 
StartingForkPoolWorker-31
Starting 4b8b10d03552e0891898dfa8eb8eefff.objdaee5cf285b8d210eeb8d422649e5f2b.objd7ba704184d424dfd56d9106430c3fe.obj43e1cabc5dd2fa91fffc97a61124b1a9.objForkPoolWorker-32962

In [1]:
import os
from os import path
import h5py
import numpy as np

from scipy.spatial import cKDTree as KDTree

In [2]:
filename_list = [fn for fn in os.listdir('evals/shape/PIFO_2') if fn.endswith('.hdf5')]

for num_views in [2, 8]:
    for filename in filename_list:
        with h5py.File(path.join('evals/shape/gt', filename), 'r') as f:
            surface_points_gt = f['surface_points'][:]
            sdf_gt = f['sdf'][:]

        for exp_name in ['PIFO', 'noPixel', 'vecObj']:
            with h5py.File(path.join('evals/shape', exp_name+'_'+str(num_views), filename), 'r+') as f:
                surface_points_pred = f['surface_points'][:]
                sdf_pred = f['sdf'][:]

                d_sdf = np.mean(np.abs(sdf_gt-sdf_pred))
#                 del f['sdf_error']
                f.create_dataset("sdf_error", data=d_sdf)

                intersection = np.logical_and(sdf_gt<0, sdf_pred<0)
                union = np.logical_or(sdf_gt<0, sdf_pred<0)

                IoU = intersection.sum()/union.sum()
#                 del f['IoU']
                f.create_dataset("IoU", data=IoU)

                # one direction
                gen_points_kd_tree = KDTree(surface_points_pred)
                one_distances, one_vertex_ids = gen_points_kd_tree.query(surface_points_gt)
                gt_to_gen_chamfer = np.mean(np.abs(one_distances))

                # other direction
                gt_points_kd_tree = KDTree(surface_points_gt)
                two_distances, two_vertex_ids = gt_points_kd_tree.query(surface_points_pred)
                gen_to_gt_chamfer = np.mean(np.abs(two_distances))

                chamfer_dist = gt_to_gen_chamfer + gen_to_gt_chamfer
#                 del f['chamfer_dist']
                f.create_dataset("chamfer_dist", data=chamfer_dist)


In [4]:
with h5py.File('data/split.hdf5', 'r') as f:
    train_list = f['train'][:]
    test_list = f['test'][:]
    
for num_views in [2, 4, 8]:
    print('======================== '+str(num_views)+' ========================')
    for file_list in [train_list, test_list]:
        exp_names = ['PIFO', 'noPixel', 'vecObj']
        sdf_error_list = np.zeros(3)
        IoU_list = np.zeros(3)
        chamfer_list = np.zeros(3)
        for filename_ in file_list:
            filename = path.splitext(filename_)[0] + '.hdf5'
            for i, exp_name in enumerate(exp_names):
                with h5py.File(path.join('evals/shape', exp_name+'_'+str(num_views), filename), 'r') as f:
                    sdf = f['sdf'][:].reshape(100,100,100)[50]
                    sdf_error_list[i] += f['sdf_error'][()]
                    IoU_list[i] += f['IoU'][()]
                    chamfer_list[i] += f['chamfer_dist'][()]

        print(sdf_error_list/len(file_list))
        print(IoU_list/len(file_list))
        print(chamfer_list/len(file_list))
        
        print('================================================')

======================== 2 ========================
[0.00291221 0.00358016 0.01564517]
[0.76030017 0.64234854 0.04467663]
[0.00613739 0.00849832 0.03909729]
[0.00463603 0.00495956 0.01576692]
[0.57701976 0.51533249 0.0462498 ]
[0.00883815 0.01077625 0.04038378]
======================== 4 ========================
[0.0022018  0.00281574 0.01502967]
[0.81631658 0.69712199 0.03643675]
[0.00525729 0.00742142 0.03860936]
[0.00338077 0.00392534 0.01523811]
[0.6560379  0.58085512 0.01400092]
[0.00689576 0.00948962 0.039687  ]
======================== 8 ========================
[0.00168339 0.0023089  0.01463815]
[0.85121499 0.72812803 0.03344475]
[0.0047822  0.00674826 0.03866058]
[0.00272428 0.00351263 0.01526232]
[0.6828652  0.60663545 0.00648325]
[0.00634309 0.00879626 0.04063226]


In [6]:
for t, dataset in enumerate(['a', 'b']):
    print(t==0)

True
False


In [ ]:
[0.0022018  0.00281574 0.01502967]
[0.81631658 0.69712199 0.03643675]
[0.00525729 0.00742142 0.03860936]

In [ ]:
[0.00338077 0.00392534 0.01523811]
[0.6560379  0.58085512 0.01400092]
[0.00689576 0.00948962 0.039687  ]


In [74]:
# dataset = trainset
dataset = testset

T = np.eye(4)
ind=3
data = to_device(dataset[ind], device)
rgb, projections = warper(data['rgb'][:].unsqueeze(0), 
                          data['cam_extrinsic'][:].unsqueeze(0), 
                          data['cam_intrinsic'][:].unsqueeze(0))

vertices, faces, normals = obj.extract_mesh(rgb,
                                            projections, 
                                            scale=.2, 
                                            delta=0.005,
                                            sdf_scale=C['SDF_SCALE'],
                                            draw=draw_mesh)
render_images = rgb.squeeze(0).cpu()
num_views = render_images.shape[0]
fig = plt.figure()
for i in range(num_views):
    ax = plt.subplot(1,num_views,i+1)
    ax.imshow(render_images[i,...].permute(1,2,0))
plt.tight_layout()
plt.show()
mesh = trimesh.Trimesh(vertices=vertices, 
                       faces=faces).apply_transform(T)
print(mesh.is_watertight)
mesh.visual.vertex_colors = [.5, .5, 1.]

# T[2,3] = .3
true_mesh = trimesh.load('../dataGeneration_vF/data/meshes_coll/'+data['filenames']).apply_transform(T)
true_mesh.visual.vertex_colors = [1., .5, .5]

trimesh.Scene([mesh+true_mesh]).show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

True


In [75]:
point_cloud = mesh_to_sdf.get_surface_point_cloud(mesh, 
                                                  bounding_radius=0.15, 
                                                  calculate_normals=False)

In [76]:
np.linalg.norm(true_mesh.vertices, axis=1).max()

0.11247708691995896

In [77]:
pts = point_cloud.get_random_surface_points(500)
mesh_list = []
T = np.eye(4)
mesh_list.append(trimesh.creation.icosphere(radius=0.01).apply_transform(T))
for i in range(pts.shape[0]):
    T[:3,3] = pts[i]
    mesh_list.append(trimesh.creation.icosphere(radius=0.01).apply_transform(T))
trimesh.Scene(mesh_list).show()

In [41]:
%matplotlib widget
plt.figure(figsize=(7,7))
ax = plt.subplot(111, projection='3d')
ax.scatter(pts[:,0],pts[:,1],pts[:,2],s=100)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …